In [1]:
import pandas as pd
pd.options.display.float_format = '{:,.3f}'.format
import numpy as np

import warnings
warnings.filterwarnings('ignore')
#plotting
import plotly
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
import plotly.figure_factory as ff


import cufflinks as cf
init_notebook_mode(connected=True)
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

import matplotlib.pyplot as plt
%matplotlib inline
import datetime

import os

In [2]:
import seaborn as sns

from IPython.display import Image
from IPython.core.display import display, HTML, Markdown
from IPython.display import display_html 

In [3]:
#makes numbers as strings so they can fit the table
def human_format(num, percentage=False):
    if num>=1:
        num = float('{:.3g}'.format(num))
        magnitude = 0
        while abs(num) >= 1000:
            magnitude += 1
            num /= 1000.0
        return '{}{}'.format('{:f}'.format(num).rstrip('0').rstrip('.'\
    ), ['', 'K', 'M', 'B', 'T'][magnitude])
    elif num<=-1:
        num = float('{:.3g}'.format(num*-1))
        magnitude = 0
        while abs(num) >= 1000:
            magnitude += 1
            num /= 1000.0
        return '-{}{}'.format('{:f}'.format(num).rstrip('0').rstrip('.'\
    ), ['', 'K', 'M', 'B', 'T'][magnitude])
    else:
        if percentage:
            return "{0:.0%}".format(num*1.0)
        else:
            return "{0:.3}".format(num*1.0)

In [4]:
backtest_folder = r'Backtest'

In [5]:
#csv

In [6]:
df = pd.DataFrame()
for file_name in [x for x in os.listdir(backtest_folder) if '.csv' in x]:
    df_part = pd.read_csv(backtest_folder+r'\\'+file_name, encoding='utf-8')
    df = pd.concat([df,df_part])

In [7]:
#formatting
for column in ['total_pnl','mean_pnl','max pnl', 'min pnl', 'std pnl','mean_pnl_winners',
               'mean_pnl_losers','avg $ move']:
    df[column] = df[column].apply(lambda x: '${:,.1f}'.format(x))
    
for column in ['sharpe_ratio']:
    df[column] = df[column].apply(lambda x: '{:,.1f}'.format(x))

for column in ['avg tick move']:
    df[column] = df[column].apply(lambda x: '{:,.1f}'.format(x))
    
for column in ['momentum_threshold']:
    df[column] = df[column].apply(lambda x: '{:,.4%}'.format(x/100))
    
for column in ['days_traded %','Win %']:
    df[column] = df[column].apply(lambda x: '{:,.1%}'.format(x))

In [8]:
df.to_csv(r'results_all.csv', encoding= 'utf-8', index=False)

In [9]:
#selected

In [10]:
df = pd.DataFrame()
for file_name in [x for x in os.listdir(backtest_folder) if '.csv' in x]:
    df_part = pd.read_csv(backtest_folder+r'\\'+file_name, encoding='utf-8')
    df = pd.concat([df,df_part])

In [11]:
df = df[(df['Win %']>0.55)&(df['sharpe_ratio']>2)].copy()

In [12]:
#formatting
for column in ['total_pnl','mean_pnl','max pnl', 'min pnl', 'std pnl','mean_pnl_winners',
               'mean_pnl_losers','avg $ move']:
    df[column] = df[column].apply(lambda x: '${:,.1f}'.format(x))
    
for column in ['sharpe_ratio']:
    df[column] = df[column].apply(lambda x: '{:,.1f}'.format(x))

for column in ['avg tick move']:
    df[column] = df[column].apply(lambda x: '{:,.1f}'.format(x))
    
for column in ['momentum_threshold']:
    df[column] = df[column].apply(lambda x: '{:,.4%}'.format(x/100))
    
for column in ['days_traded %','Win %']:
    df[column] = df[column].apply(lambda x: '{:,.1%}'.format(x))

In [13]:
df.to_csv(r'results_win_55_sharpe_2.csv', encoding= 'utf-8', index=False)

In [14]:
#report

# Report by ticker and direction (all)

In [42]:
df = pd.DataFrame()
for file_name in [x for x in os.listdir(backtest_folder) if '.csv' in x]:
    df_part = pd.read_csv(backtest_folder+r'\\'+file_name, encoding='utf-8')
    df = pd.concat([df,df_part])
    

In [39]:
df['direction'] = df['momentum_threshold'].apply(lambda x: 'Long' if x>=0 else 'Short')
df_part = df.groupby(['ticker','direction']).agg({'total_pnl':'sum','mean_pnl':'mean','sharpe_ratio':'mean',
                                       'Win %':'mean','ticker':'count',})
df_part.columns = ['Total Pnl','Avg Pnl','Sharpe','Win %','Count Entries']

In [40]:
df_part = df_part.style\
                 .background_gradient(cmap='Blues')\
                 .apply(lambda x: ["color: red" if '-' in str(v)  else "" for v in x], axis = 1)\
                 .format({
                    'Total Pnl': '${:,.0f}'.format,
                    'Avg Pnl': '${:,.1f}'.format,
                    'Sharpe': '{:,.1f}'.format,
                    'Win %': '{:,.1%}'.format,
                     'Count Entries': '{:,.0f}'.format})
display(df_part)

# Report by ticker and direction (Win % > 55 and Sharpe>2)

In [20]:
df = pd.DataFrame()
for file_name in [x for x in os.listdir(backtest_folder) if '.csv' in x]:
    df_part = pd.read_csv(backtest_folder+r'\\'+file_name, encoding='utf-8')
    df = pd.concat([df,df_part])
    
df = df[(df['Win %']>0.55)&(df['sharpe_ratio']>2)].copy()

In [21]:
df['direction'] = df['momentum_threshold'].apply(lambda x: 'Long' if x>=0 else 'Short')

In [22]:
df_part = df.groupby(['ticker','direction']).agg({'total_pnl':'sum','mean_pnl':'mean','sharpe_ratio':'mean',
                                       'Win %':'mean','ticker':'count',})
df_part.columns = ['Total Pnl','Avg Pnl','Sharpe','Win %','Count Entries']

In [23]:
df_part = df_part.style\
                 .background_gradient(cmap='summer')\
                 .format({
                    'Total Pnl': '${:,.0f}'.format,
                    'Avg Pnl': '${:,.1f}'.format,
                    'Sharpe': '{:,.1f}'.format,
                    'Win %': '{:,.1%}'.format })
display(df_part)

# Report by time and threshold (Win % > 55 and Sharpe>2)

In [24]:
df = pd.DataFrame()
for file_name in [x for x in os.listdir(backtest_folder) if '.csv' in x]:
    df_part = pd.read_csv(backtest_folder+r'\\'+file_name, encoding='utf-8')
    df = pd.concat([df,df_part])

In [25]:
df = df[(df['Win %']>0.55)&(df['sharpe_ratio']>2)].copy()

In [26]:
for ticker in df['ticker'].unique():
    display(HTML(f'<H2>{ticker}</H2>'))
    df_part = df[df['ticker']==ticker].copy()
    
    df_part = df_part.drop_duplicates(subset=['entry_momentum','exit_momentum','exit_pnl','momentum_threshold'])
    df_part = df_part.groupby(['entry_momentum','exit_momentum','exit_pnl','momentum_threshold'])\
                [['mean_pnl','sharpe_ratio','Win %','days_traded']].mean()
#     df_part['mean_pnl'] = df_part['mean_pnl'].apply(lambda x: '${:,.1f}'.format(x))
#     df_part['sharpe_ratio'] = df_part['sharpe_ratio'].apply(lambda x: '{:,.1f}'.format(x))
#     df_part['Win %'] = df_part['Win %'].apply(lambda x: '{:,.1%}'.format(x))
    #df_part['days_traded'] = df_part['days_traded'].apply(lambda x: '{:,.0f}'.format(x))
    df_part.columns = ['Avg Pnl','Sharpe','Win %','Count Trades']
    df_part.index.names = ['Momentum Entry','Momentum Exit','PnL Exit','Threshold']
    df_part = df_part.sort_index(ascending = (False, True, True))
    df_part = df_part.reset_index()

    for column in ['Momentum Entry','Momentum Exit','PnL Exit']:
        df_part[column] = df_part[column].apply(lambda x: '{:,.0f}'.format(x))
    df_part = df_part.sort_values(by='Sharpe', ascending = False)
    df_part['Threshold'] = df_part['Threshold'].apply(lambda x: '{:,.4%}'.format(x/100))
    
    df_part = df_part.style\
                 .background_gradient(cmap='summer')\
                 .format({
                    'Avg Pnl': '${:,.1f}'.format,
                    'Sharpe': '{:,.1f}'.format,
                    'Win %': '{:,.1%}'.format })\
                .hide_index()
    display(df_part)

In [179]:
# for ticker in df['ticker'].unique():
#     display(HTML(f'<H2>{ticker}</H2>'))
#     df_part = df[df['ticker']==ticker].copy()
    
#     df_part = df_part.drop_duplicates(subset=['entry_momentum','exit_momentum','exit_pnl','momentum_threshold'])
#     df_part = df_part.groupby(['entry_momentum','exit_momentum','exit_pnl','momentum_threshold'])\
#                 [['mean_pnl','sharpe_ratio','days_traded']].mean()
#     df_part['mean_pnl'] = df_part['mean_pnl'].apply(lambda x: '${:,.1f}'.format(x))
#     df_part['sharpe_ratio'] = df_part['sharpe_ratio'].apply(lambda x: '{:,.1f}'.format(x))
#     df_part['days_traded'] = df_part['days_traded'].apply(lambda x: '{:,.0f}'.format(x))
#     df_part.columns = ['Avg Pnl','Sharpe','Count']
#     df_part.index.names = ['Momentum Entry','Momentum Exit','PnL Exit','Threshold']
#     df_part = df_part.sort_index(ascending = (False, True, True))
#     df_part = df_part.reset_index()

#     for column in ['Momentum Entry','Momentum Exit','PnL Exit']:
#         df_part[column] = df_part[column].apply(lambda x: '{:,.0f}'.format(x))
        
#     df_part['id'] = df_part[['Momentum Entry','Momentum Exit']]\
#                     .apply(lambda x: x[0]+'_'+x[1], axis=1)
#     for uid in df_part['id'].unique():
#         #print(uid)
#         df_report = df_part[df_part['id']==uid].copy()
#         entry_momentum = df_report['Momentum Entry'].values[0]
#         exit_momentum = df_report['Momentum Exit'].values[0]
#         exit_pnl = df_report['PnL Exit'].values[0]
        
#         print('Ticker: {0}; Momentum Start:  {1}; Momentum End: {2}; Enter Trade: {3}'\
#               .format(ticker, entry_momentum, exit_momentum, exit_momentum))
            
# #         df_report = df_report.groupby('Threshold')\
# #                     [['Avg Pnl','Sharpe','Count']].max()\
# #                     .transpose()
#         summary_container = []
#         i=0
#         for caption in ['Avg Pnl','Sharpe','Count']:
#             i=i+1
#             df_pivot = pd.pivot_table(df_report, index = 'PnL Exit',
#                                       columns = 'Threshold',
#                                       values = caption, aggfunc = lambda x: x)\
#                        .transpose()
#             df_pivot.index = ['{:,.4%}'.format(x/100) for x in df_pivot.index]
#             df_pivot['']=''
#             if i==1:
#                 summary_container.append(df_pivot.style\
#                 .apply(lambda x: ["color: red" if '-' in v  else "" for v in x], axis = 1)\
#                 .set_table_attributes("style='display:inline'").set_caption(caption))
#             else:
#                 summary_container.append(df_pivot.style\
#                 .apply(lambda x: ["color: red" if '-' in v  else "" for v in x], axis = 1)\
#                 .set_table_attributes("style='display:inline'").set_caption(caption))

#         display_html(summary_container[0]._repr_html_()+
#                      summary_container[1]._repr_html_()+
#                      summary_container[2]._repr_html_(), raw=True)

In [41]:
!jupyter nbconvert --to html --TemplateExporter.exclude_input=True --template toc2 "MomentumProjectReport.ipynb"

[NbConvertApp] Converting notebook MomentumProjectReport.ipynb to html
[NbConvertApp] Writing 6463412 bytes to MomentumProjectReport.html
